<a href="https://colab.research.google.com/github/sgraziano26/Coursera_Capstone/blob/master/CourseraCapstone.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [47]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import OneHotEncoder, MinMaxScaler
from sklearn.compose import  ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.ensemble import RandomForestClassifier
from sklearn.neighbors import NearestNeighbors
from sklearn.neighbors import KNeighborsClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import jaccard_similarity_score
from sklearn.metrics import f1_score
from sklearn.metrics import log_loss

In [48]:
#Import Dataset
df = pd.read_csv("Collisions.csv")
df.shape

/usr/local/lib/python3.6/dist-packages/IPython/core/interactiveshell.py:2718: DtypeWarning: Columns (35) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


(221524, 40)

In [49]:
#Feature Selection
df1 = df.copy()
df1.dtypes

#Drop columns
df1.drop(['X','Y','OBJECTID','INCKEY','COLDETKEY','REPORTNO','STATUS','INTKEY','LOCATION','EXCEPTRSNCODE','EXCEPTRSNDESC','SEVERITYDESC','INCDATE','INCDTTM','SDOT_COLDESC','SDOTCOLNUM','ST_COLDESC','SEGLANEKEY','CROSSWALKKEY','ST_COLCODE','SDOT_COLCODE'], axis = 1, inplace=True)

#Change all object fields to lower case for consistency
df1['ADDRTYPE'] = df1['ADDRTYPE'].str.lower()
df1['JUNCTIONTYPE'] = df1['JUNCTIONTYPE'].str.lower()
df1['WEATHER'] = df1['WEATHER'].str.lower()
df1['COLLISIONTYPE'] = df1['COLLISIONTYPE'].str.lower()
df1['ROADCOND'] = df1['ROADCOND'].str.lower()
df1['LIGHTCOND'] = df1['LIGHTCOND'].str.lower()
df1['HITPARKEDCAR'] = df1['HITPARKEDCAR'].str.lower()
df1['SPEEDING'] = df1['SPEEDING'].str.lower()
df1['INATTENTIONIND'] = df1['INATTENTIONIND'].str.lower()
df1['UNDERINFL'] = df1['UNDERINFL'].str.lower()
df1['PEDROWNOTGRNT'] = df1['PEDROWNOTGRNT'].str.lower()

#Turning Flags to Numeric
df1.UNDERINFL.replace(to_replace=['n', 'y'], value=[0, 1], inplace=True)
df1.INATTENTIONIND.replace(to_replace=[ np.NaN, 'y'], value=[0, 1], inplace=True)
df1.HITPARKEDCAR.replace(to_replace=['n', 'y'], value=[0, 1], inplace=True)
df1.SPEEDING.replace(to_replace=['y',  np.NaN], value=[1, 0], inplace=True)
df1.PEDROWNOTGRNT.replace(to_replace=[ np.NaN, 'y'], value=[0, 1], inplace=True)
df1.UNDERINFL =df1.UNDERINFL.astype(float)

#Create target variable and category variables
y1 = ['SEVERITYCODE']
flags1 = ['INATTENTIONIND','UNDERINFL','SPEEDING']#,'HITPARKEDCAR','PEDROWNOTGRNT']
cat_columns1 = ['ROADCOND','LIGHTCOND','WEATHER']#'COLLISIONTYPE','ADDRTYPE','JUNCTIONTYPE',]
numeric_columns1 = ['VEHCOUNT']#,'FATALITIES','PEDCYLCOUNT','SERIOUSINJURIES','PERSONCOUNT','PEDCOUNT','INJURIES']

from sklearn.impute import SimpleImputer
for f in cat_columns1:
  print(f, df1[f].unique())


ROADCOND ['dry' 'wet' nan 'unknown' 'ice' 'other' 'snow/slush' 'standing water'
 'oil' 'sand/mud/dirt']
LIGHTCOND ['daylight' 'dark - street lights on' nan 'dark - no street lights' 'dawn'
 'unknown' 'dark - street lights off' 'dusk' 'other'
 'dark - unknown lighting']
WEATHER ['clear' 'overcast' nan 'raining' 'unknown' 'sleet/hail/freezing rain'
 'other' 'snowing' 'fog/smog/smoke' 'blowing sand/dirt' 'severe crosswind'
 'partly cloudy' 'blowing snow']


In [50]:
#Feature Selection Continued
#Imputing
imp1 = SimpleImputer(missing_values=np.nan, strategy='most_frequent')
imp3 =  SimpleImputer(missing_values=np.nan, strategy='mean')
cat_cols1 = pd.DataFrame(imp1.fit_transform(df1[flags1+cat_columns1]), columns=flags1+cat_columns1)
num_cols1 = pd.DataFrame(imp3.fit_transform(df1[numeric_columns1]), columns  = numeric_columns1)
fdf1 = pd.concat([cat_cols1, num_cols1], axis = 1)

#One Hot Encoding
end1 = OneHotEncoder(sparse=False)
new_cat1 = end1.fit_transform(fdf1[cat_columns1])
cat_names1 = end1.get_feature_names(input_features = cat_columns1)
cat_col_end1 = pd.DataFrame(new_cat1, columns = cat_names1)

#Min Max Scaler
scl1 = MinMaxScaler()
scl1.fit(fdf1[numeric_columns1])
dat1 = scl1.transform(fdf1[numeric_columns1])
num_col_scl1 = pd.DataFrame(dat1, columns = numeric_columns1)

#Concatenate into a variable all preprocessed columns
fdf1 = pd.concat([fdf1[flags1],cat_col_end1,num_col_scl1], axis = 1)

df1.SEVERITYCODE.replace(to_replace=[np.nan], value=['1'], inplace=True)
df1.SEVERITYCODE.isnull().sum()

mdl1 = RandomForestClassifier()
mdl1.fit(fdf1, df1.SEVERITYCODE)
mdl1.score(fdf1, df1.SEVERITYCODE)

importance1 = pd.DataFrame(mdl1.feature_importances_)

importance1['cols'] = fdf1.columns

importance1.columns = ['Imp','cols']
importance1.sort_values(by = 'Imp', ascending=False)

Imp                                cols
33  0.782220                            VEHCOUNT
17  0.030170                  LIGHTCOND_daylight
10  0.027040                    ROADCOND_unknown
32  0.021376                     WEATHER_unknown
20  0.019710                   LIGHTCOND_unknown
23  0.017719                       WEATHER_clear
3   0.016376                        ROADCOND_dry
0   0.015989                      INATTENTIONIND
2   0.012873                            SPEEDING
14  0.011256   LIGHTCOND_dark - street lights on
11  0.009720                        ROADCOND_wet
1   0.008601                           UNDERINFL
26  0.007301                    WEATHER_overcast
28  0.004348                     WEATHER_raining
18  0.002625                      LIGHTCOND_dusk
12  0.001606   LIGHTCOND_dark - no street lights
16  0.001381                      LIGHTCOND_dawn
4   0.001380                        ROADCOND_ice
8   0.001134                 ROADCOND_snow/slush
13  0.001104  LIGHTCOND_dark - street lights off
24  0.001056              WEATHER_fog/smog/smoke
31  0.000892                     WEATHER_snowing
25  0.000859                       WEATHER_other
19  0.000579                     LIGHTCOND_other
6   0.000501                      ROADCOND_other
30  0.000483    WEATHER_sleet/hail/freezing rain
9   0.000398             ROADCOND_standing water
5   0.000312                        ROADCOND_oil
7   0.000281              ROADCOND_sand/mud/dirt
21  0.000240           WEATHER_blowing sand/dirt
29  0.000171            WEATHER_severe crosswind
27  0.000130               WEATHER_partly cloudy
15  0.000125   LIGHTCOND_dark - unknown lighting
22  0.000045                WEATHER_blowing snow

In [51]:
#After Feature Selection, Begin Data Modeling
#Create Copy of Dataframe
df2 = df.copy()
print(df2.shape)

(221524, 40)


In [52]:
#Drop Columns
df2.drop(['X','Y','OBJECTID','INCKEY','COLDETKEY','REPORTNO','STATUS','INTKEY','LOCATION','EXCEPTRSNCODE','EXCEPTRSNDESC','SEVERITYDESC','INCDATE','INCDTTM','SDOT_COLDESC','SDOTCOLNUM','ST_COLDESC','SEGLANEKEY','CROSSWALKKEY','ST_COLCODE','SDOT_COLCODE'], axis = 1, inplace=True)


In [53]:
#Change all object fields to lower case for consistency
df2['ADDRTYPE'] = df2['ADDRTYPE'].str.lower()
df2['JUNCTIONTYPE'] = df2['JUNCTIONTYPE'].str.lower()
df2['WEATHER'] = df2['WEATHER'].str.lower()
df2['COLLISIONTYPE'] = df2['COLLISIONTYPE'].str.lower()
df2['ROADCOND'] = df2['ROADCOND'].str.lower()
df2['LIGHTCOND'] = df2['LIGHTCOND'].str.lower()
df2['HITPARKEDCAR'] = df2['HITPARKEDCAR'].str.lower()
df2['SPEEDING'] = df2['SPEEDING'].str.lower()
df2['INATTENTIONIND'] = df2['INATTENTIONIND'].str.lower()
df2['UNDERINFL'] = df2['UNDERINFL'].str.lower()
df2['PEDROWNOTGRNT'] = df2['PEDROWNOTGRNT'].str.lower()

In [54]:
#Turning Flags to Numeric
df2.UNDERINFL.replace(to_replace=['n', 'y'], value=[0, 1], inplace=True)
df2.INATTENTIONIND.replace(to_replace=[ np.NaN, 'y'], value=[0, 1], inplace=True)
df2.HITPARKEDCAR.replace(to_replace=['n', 'y'], value=[0, 1], inplace=True)
df2.SPEEDING.replace(to_replace=['y',  np.NaN], value=[1, 0], inplace=True)
df2.PEDROWNOTGRNT.replace(to_replace=[ np.NaN, 'y'], value=[0, 1], inplace=True)
df2.UNDERINFL =df2.UNDERINFL.astype(float)

In [55]:
#Create Target Variable and Predictor Variables
target = ['SEVERITYCODE']
flags = ['INATTENTIONIND','UNDERINFL','SPEEDING']
cat_columns = ['ROADCOND','LIGHTCOND','WEATHER']
numeric_columns = ['VEHCOUNT']
X = df2[flags+cat_columns+numeric_columns]
y = df2[target]

In [56]:
#Split into Train / Test Sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.33, random_state=42, stratify=y)
print ('Train set:', X_train.shape,  y_train.shape)
print ('Test set:', X_test.shape,  y_test.shape)

Train set: (148421, 7) (148421, 1)
Test set: (73103, 7) (73103, 1)


In [57]:
#Categorical Data
imp = SimpleImputer(missing_values=np.nan, strategy='most_frequent')
ohe = OneHotEncoder()

#Numeric Data 
imp2 =  SimpleImputer(missing_values=np.nan, strategy='mean')
scl = MinMaxScaler()

categorical_transformer = Pipeline(steps=[
    ('imputer', imp),
    ('onehot', ohe)
    ])

numeric_transformer = Pipeline(steps=[
    ('imputer', imp2),
    ('scaler', scl)
    ])

preprocessor = ColumnTransformer(
    transformers=[
        ('cat', categorical_transformer, flags+cat_columns),
        ('num', numeric_transformer, numeric_columns),
        ], remainder = 'drop')


In [58]:
#Create KNN Model
clf_knn = Pipeline(steps=[('preprocessor', preprocessor),
                      ('classifier', KNeighborsClassifier())])

In [59]:
#Create Decision Tree Classifier Model
clf_dt = Pipeline(steps=[('preprocessor', preprocessor),
                      ('classifier', DecisionTreeClassifier())])

In [60]:
#Create Logistic Regression Model
clf_lr = Pipeline(steps=[('preprocessor', preprocessor),
                      ('classifier', LogisticRegression())])

In [61]:
#Train and Test KNN Model
clf_knn.fit(X_train, y_train)
clf_knn.score(X_train, y_train)
knn_model = clf_knn.predict(X_test)
print("KNN Jaccard Score: %.2f" % clf_knn.score(X_test, y_test))
print("KNN F1-score: %.2f" % f1_score(y_test, knn_model, average='weighted'))


/usr/local/lib/python3.6/dist-packages/sklearn/pipeline.py:354: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  self._final_estimator.fit(Xt, y, **fit_params)


KNN Jaccard Score: 0.69
KNN F1-score: 0.64


In [62]:
#Train and Test Decision Tree Classifier Model
clf_dt.fit(X_train, y_train)
clf_dt.score(X_train, y_train)
dt_model = clf_dt.predict(X_test)
print("DT Jaccard Score: %.2f" % clf_dt.score(X_test, y_test))
print("DT F1-score: %.2f" % f1_score(y_test, dt_model, average='weighted'))

DT Jaccard Score: 0.72
DT F1-score: 0.67


In [63]:
#Train and Test Logistic Regression Model
clf_lr.fit(X_train, y_train)
clf_lr.score(X_train, y_train)
lr_model = clf_lr.predict(X_test)
print("LR Jaccard Score: %.2f" % clf_lr.score(X_test, y_test))
print("LR F1-score: %.2f" % f1_score(y_test, lr_model, average='weighted'))

/usr/local/lib/python3.6/dist-packages/sklearn/utils/validation.py:760: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/usr/local/lib/python3.6/dist-packages/sklearn/linear_model/_logistic.py:940: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  extra_warning_msg=_LOGISTIC_SOLVER_CONVERGENCE_MSG)


LR Jaccard Score: 0.70
LR F1-score: 0.59


In [69]:
#Create Dataframe for Folium Map
df3 = df.copy()
df3.drop(['OBJECTID','INCKEY','COLDETKEY','REPORTNO','STATUS','INTKEY','LOCATION','EXCEPTRSNCODE','EXCEPTRSNDESC','SEVERITYDESC','INCDATE','INCDTTM','SDOT_COLDESC','SDOTCOLNUM','ST_COLDESC','SEGLANEKEY','CROSSWALKKEY','ST_COLCODE','SDOT_COLCODE'], axis = 1, inplace=True)
df3.dropna(subset=['X', 'Y'], inplace=True)
df3.shape

(214049, 21)

In [70]:
#Import Folium
!conda install -c conda-forge folium=0.5.0 --yes
import folium

print('Folium installed and imported!')

/bin/bash: conda: command not found
Folium installed and imported!


In [73]:
#Define Seattle, Washington Map
seattle_map = folium.Map(location=[47.655548, -122.3032], zoom_start=12)

#Display World Map
seattle_map

In [74]:
# get the first 10000 crimes in the df_incidents dataframe
limit = 10000
df3 = df3.iloc[0:limit, :]
df3.shape

(10000, 21)

In [75]:
# instantiate a feature group for the incidents in the dataframe
incidents = folium.map.FeatureGroup()

# loop through the 100 crimes and add each to the incidents feature group
for lat, lng, in zip(df3.Y, df3.X):
    incidents.add_child(
        folium.Circle(
            [lat, lng],
            radius=5, # define how big you want the circle markers to be
            color='blue',
            fill=True,
            fill_color='blue',
            fill_opacity=0.6
        )
    )

# add incidents to map
seattle_map.add_child(incidents)